In [ ]:
from google.colab import drive
drive.mount('/content/drive/')

Mounted at /content/drive/


In [ ]:
# import the necessary libraries

import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from numpy import random
from sklearn.preprocessing import OrdinalEncoder


In [ ]:
data = pd.read_csv('/content/drive/My Drive/CS412/Project/german_credit_data.csv') # enter the file path on your drive for the csv file
data.head() # print first 5 rows to check the data

Unnamed: 0  Age     Sex  Job Housing Saving accounts Checking account  \
0           0   67    male    2     own             NaN           little   
1           1   22  female    2     own          little         moderate   
2           2   49    male    1     own          little              NaN   
3           3   45    male    2    free          little           little   
4           4   53    male    2    free          little           little   

   Credit amount  Duration              Purpose  Risk  
0           1169         6             radio/TV  good  
1           5951        48             radio/TV   bad  
2           2096        12            education  good  
3           7882        42  furniture/equipment  good  
4           4870        24                  car   bad

In [ ]:
#First we must handle NA values of our dataset. Since we are dealing with categorical valiables,
#we choose to implement a mode imputation technique
data['Saving accounts'] = data['Saving accounts'].fillna(data['Saving accounts'].mode()[0])
data['Checking account'] = data['Checking account'].fillna(data['Checking account'].mode()[0])

data.head() # print first 5 rows to check the data

Unnamed: 0  Age     Sex  Job Housing Saving accounts Checking account  \
0           0   67    male    2     own          little           little   
1           1   22  female    2     own          little         moderate   
2           2   49    male    1     own          little           little   
3           3   45    male    2    free          little           little   
4           4   53    male    2    free          little           little   

   Credit amount  Duration              Purpose  Risk  
0           1169         6             radio/TV  good  
1           5951        48             radio/TV   bad  
2           2096        12            education  good  
3           7882        42  furniture/equipment  good  
4           4870        24                  car   bad

In [ ]:
# Define the order of your categories
housing_encode = [['free', 'rent', 'own']] # free = 0.0 /// rent = 1.0 /// own = 2.0
saving_encode = [['little', 'moderate', 'quite rich', 'rich']] # little = 0.0 /// moderate = 1.0 /// quite rich = 2.0 /// rich = 3.0
checking_encode = [['little', 'moderate', 'rich']] # little = 0.0 /// moderate = 1.0 /// rich = 2.0
risk_encode = [['good', 'bad']] # good = 0.0 /// bad = 1.0


# Create the encoder
ordinal_encoder_housing = OrdinalEncoder(categories=housing_encode)
ordinal_encoder_saving = OrdinalEncoder(categories=saving_encode)
ordinal_encoder_checking = OrdinalEncoder(categories=checking_encode)
ordinal_encoder_risk = OrdinalEncoder(categories=risk_encode)

# Fit and transform the data and replace the column in the dataframe
data['Housing'] = ordinal_encoder_housing.fit_transform(data[['Housing']])
data['Saving accounts'] = ordinal_encoder_saving.fit_transform(data[['Saving accounts']])
data['Checking account'] = ordinal_encoder_checking.fit_transform(data[['Checking account']])
data['Risk'] = ordinal_encoder_risk.fit_transform(data[['Risk']])

print(data.head())  # print first 5 rows to check the data


   Unnamed: 0  Age     Sex  Job  Housing  Saving accounts  Checking account  \
0           0   67    male    2      2.0              0.0               0.0   
1           1   22  female    2      2.0              0.0               1.0   
2           2   49    male    1      2.0              0.0               0.0   
3           3   45    male    2      0.0              0.0               0.0   
4           4   53    male    2      0.0              0.0               0.0   

   Credit amount  Duration              Purpose  Risk  
0           1169         6             radio/TV   0.0  
1           5951        48             radio/TV   1.0  
2           2096        12            education   0.0  
3           7882        42  furniture/equipment   0.0  
4           4870        24                  car   1.0  


In [ ]:
# Since seks and purpose variables are not an ordered categorical data (they cannot be put in a logical order),
# we implemented one-hot encoding insted of the previous ordinal encoding for these

data = pd.get_dummies(data, columns=['Sex'], prefix='Sex')
data = pd.get_dummies(data, columns=['Purpose'], prefix='Purpose')
print(data.head())  # print first 5 rows to check the data


   Unnamed: 0  Age  Job  Housing  Saving accounts  Checking account  \
0           0   67    2      2.0              0.0               0.0   
1           1   22    2      2.0              0.0               1.0   
2           2   49    1      2.0              0.0               0.0   
3           3   45    2      0.0              0.0               0.0   
4           4   53    2      0.0              0.0               0.0   

   Credit amount  Duration  Risk  Sex_female  Sex_male  Purpose_business  \
0           1169         6   0.0           0         1                 0   
1           5951        48   1.0           1         0                 0   
2           2096        12   0.0           0         1                 0   
3           7882        42   0.0           0         1                 0   
4           4870        24   1.0           0         1                 0   

   Purpose_car  Purpose_domestic appliances  Purpose_education  \
0            0                            0       

###**KNN CLASSIFICATION STARTS!!!**

In [ ]:
#Train Validation split

from sklearn.model_selection import train_test_split

X = data.drop('Risk', axis=1)  # features
y = data['Risk']  # target

X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42) # 80/20 split

print(X_train.describe())
print(X_val.describe())
print("||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||")
print(y_train.describe())
print(y_val.describe())

       Unnamed: 0         Age        Job     Housing  Saving accounts  \
count  800.000000  800.000000  800.00000  800.000000       800.000000   
mean   497.418750   35.558750    1.93000    1.607500         0.388750   
std    289.511545   11.411587    0.65432    0.675658         0.819123   
min      0.000000   19.000000    0.00000    0.000000         0.000000   
25%    241.750000   27.000000    2.00000    1.000000         0.000000   
50%    493.500000   33.000000    2.00000    2.000000         0.000000   
75%    750.250000   42.000000    2.00000    2.000000         0.000000   
max    999.000000   75.000000    3.00000    2.000000         3.000000   

       Checking account  Credit amount    Duration  Sex_female    Sex_male  \
count        800.000000     800.000000  800.000000  800.000000  800.000000   
mean           0.390000    3360.618750   21.095000    0.317500    0.682500   
std            0.600709    2898.174863   11.807211    0.465795    0.465795   
min            0.000000     25

In [ ]:
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import accuracy_score
from sklearn.model_selection import cross_val_score

k_values = [1, 3, 5, 7, 9, 11, 13] # k values we are going to try to find the best fitting

best_mean_acc = -1
best_k = None

for k in k_values:
    model = KNeighborsClassifier(n_neighbors=k) #initilize the model
    # Perform 5-fold cross-validation on the training data
    scores = cross_val_score(model, X_train, y_train, cv=5, scoring='accuracy')

    mean_acc_score = scores.mean()
    print('Validation accuracy for k=', k, ':', mean_acc_score)

    # if mean validation accuracy is better than best_mean_acc, update best_mean_acc and best_k
    if (best_mean_acc < mean_acc_score):
        best_mean_acc = mean_acc_score
        best_k = k

# Fit the final model with the best k on the full training set and evaluate on the validation set
final_model = KNeighborsClassifier(n_neighbors=best_k)
final_model.fit(X_train, y_train)
final_y_pred = final_model.predict(X_val)
final_acc = accuracy_score(y_val, final_y_pred)

print('Best mean validation accuracy (', best_mean_acc, ') is achieved with k=', best_k)
print('The final model accuracy on validation set is: ', final_acc)


Validation accuracy for k= 1 : 0.59875
Validation accuracy for k= 3 : 0.62375
Validation accuracy for k= 5 : 0.655
Validation accuracy for k= 7 : 0.66125
Validation accuracy for k= 9 : 0.6775
Validation accuracy for k= 11 : 0.68125
Validation accuracy for k= 13 : 0.6837500000000001
Best mean validation accuracy ( 0.6837500000000001 ) is achieved with k= 13
The final model accuracy on validation set is:  0.695


###**DECISION TREES STARTS!!!!!**

In [ ]:
from sklearn.tree import DecisionTreeClassifier

#Hyper parameters:
max_depth = list(range(1,30))
min_leaf = list(range(1,100))

best_mean_acc = -1
best_depth = None
best_leaves = None


for depth in max_depth:
  for leaf in min_leaf:
    tree = DecisionTreeClassifier(max_depth=depth, min_samples_leaf=leaf) #initilize the model

    # Perform 5-fold cross-validation on the training data
    scores = cross_val_score(tree, X_train, y_train, cv=5, scoring='accuracy')

    mean_acc_score = scores.mean()
    print('Validation accuracy for depth=', depth," and min leaf=", leaf, ':', mean_acc_score)

    # if mean validation accuracy is better than best_mean_acc, update best_mean_acc and hyperparameters
    if (best_mean_acc < mean_acc_score):
        best_mean_acc = mean_acc_score
        best_depth = depth
        best_leaves = leaf

# Fit the final model with the best k on the full training set and evaluate on the validation set
tree_model = DecisionTreeClassifier(max_depth=best_depth, min_samples_leaf=best_leaves)
tree_model.fit(X_train, y_train)
tree_model_pred = tree_model.predict(X_val)
final_acc = accuracy_score(y_val, tree_model_pred)

print('Best mean validation accuracy (', best_mean_acc, ') is achieved with max depth=', best_depth, " and min leaf=", best_leaves)
print('The final model accuracy on validation set is: ', final_acc)


Validation accuracy for depth= 1  and min leaf= 1 : 0.69375
Validation accuracy for depth= 1  and min leaf= 2 : 0.69375
Validation accuracy for depth= 1  and min leaf= 3 : 0.69375
Validation accuracy for depth= 1  and min leaf= 4 : 0.69375
Validation accuracy for depth= 1  and min leaf= 5 : 0.69375
Validation accuracy for depth= 1  and min leaf= 6 : 0.69375
Validation accuracy for depth= 1  and min leaf= 7 : 0.69375
Validation accuracy for depth= 1  and min leaf= 8 : 0.69375
Validation accuracy for depth= 1  and min leaf= 9 : 0.69375
Validation accuracy for depth= 1  and min leaf= 10 : 0.69375
Validation accuracy for depth= 1  and min leaf= 11 : 0.69375
Validation accuracy for depth= 1  and min leaf= 12 : 0.69375
Validation accuracy for depth= 1  and min leaf= 13 : 0.69375
Validation accuracy for depth= 1  and min leaf= 14 : 0.69375
Validation accuracy for depth= 1  and min leaf= 15 : 0.69375
Validation accuracy for depth= 1  and min leaf= 16 : 0.69375
Validation accuracy for depth= 1 

###**MULTILAYER PERCEPTRON!!!!!!!!!**

In [ ]:
from sklearn.neural_network import MLPClassifier
from sklearn.metrics import accuracy_score

hidden_layer_list = list(range(10, 101, 5))
epoch_list = list(range(200, 500, 50))
learning_rate = [0.1, 0.01, 0.001, 0.0001]

best_mean_acc = -1
best_lr = None
best_epoch = None
best_layer = None

for lr in learning_rate:
  for epoch in epoch_list:
    for layer in hidden_layer_list:
      # Initialize the MLPClassifier
      mlp = MLPClassifier(hidden_layer_sizes=(layer,), max_iter=epoch, alpha=1e-4,
                          solver='sgd', verbose=10, random_state=42,
                          learning_rate_init=lr)

      # Perform 5-fold cross-validation on the training data
      scores = cross_val_score(mlp, X_train, y_train, cv=5, scoring='accuracy')

      mean_acc_score = scores.mean()
      print('Validation accuracy for learning rate=', lr," and epoaches=", epoch, "and for layer number", layer, ':', mean_acc_score)

      # if mean validation accuracy is better than best_mean_acc, update best_mean_acc and hyperparameters
      if (best_mean_acc < mean_acc_score):
          best_mean_acc = mean_acc_score
          best_lr = lr
          best_epoch = epoch
          best_layer = layer

print('Best mean validation accuracy (', best_mean_acc, ') is achieved with learning rate=', best_lr," and epoaches=", best_epoch, "and for layer number", best_layer)

# Initialize the MLPClassifier
best_mlp = MLPClassifier(hidden_layer_sizes=(best_layer,), max_iter=best_epoch, alpha=1e-4,
                    solver='sgd', verbose=10, random_state=42,
                    learning_rate_init=best_lr)

# Train the classifier with the training data
best_mlp.fit(X_train, y_train)

# Predict the responses for the test dataset
y_pred = best_mlp.predict(X_val)

# Print the accuracy score of the MLP classifier
print('Validation accuracy: ', accuracy_score(y_val, y_pred))


Görüntülenen çıkış son 5000 satıra kısaltıldı.
Iteration 5, loss = 6.10995719
Iteration 6, loss = 6.94073257
Iteration 7, loss = 7.53787848
Iteration 8, loss = 7.91075314
Iteration 9, loss = 8.17436541
Iteration 10, loss = 8.34962399
Iteration 11, loss = 8.46585941
Iteration 12, loss = 8.54222200
Iteration 13, loss = 8.59270248
Training loss did not improve more than tol=0.000100 for 10 consecutive epochs. Stopping.
Iteration 1, loss = 13.92091503
Iteration 2, loss = 1.41096525
Iteration 3, loss = 2.12902265
Iteration 4, loss = 2.91211485
Iteration 5, loss = 3.51666192
Iteration 6, loss = 3.95249931
Iteration 7, loss = 4.25513720
Iteration 8, loss = 4.46087669
Iteration 9, loss = 4.59893988
Iteration 10, loss = 4.69057133
Iteration 11, loss = 4.75137501
Iteration 12, loss = 4.79130182
Iteration 13, loss = 4.81773669
Training loss did not improve more than tol=0.000100 for 10 consecutive epochs. Stopping.
Iteration 1, loss = 14.61026779
Iteration 2, loss = 1.34142588
Iteration 3, loss =

/usr/local/lib/python3.10/dist-packages/sklearn/neural_network/_multilayer_perceptron.py:686: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Iteration 28, loss = 0.66204689
Iteration 29, loss = 0.66117004
Iteration 30, loss = 0.66026107
Iteration 31, loss = 0.65935071
Iteration 32, loss = 0.65844225
Iteration 33, loss = 0.65758901
Iteration 34, loss = 0.65671411
Iteration 35, loss = 0.65584732
Iteration 36, loss = 0.65504764
Iteration 37, loss = 0.65425564
Iteration 38, loss = 0.65345181
Iteration 39, loss = 0.65257374
Iteration 40, loss = 0.65181752
Iteration 41, loss = 0.65105299
Iteration 42, loss = 0.65028790
Iteration 43, loss = 0.64958919
Iteration 44, loss = 0.64887535
Iteration 45, loss = 0.64820436
Iteration 46, loss = 0.64748516
Iteration 47, loss = 0.64683961
Iteration 48, loss = 0.64614951
Iteration 49, loss = 0.64544451
Iteration 50, loss = 0.64485397
Iteration 51, loss = 0.64418303
Iteration 52, loss = 0.64357551
Iteration 53, loss = 0.64292726
Iteration 54, loss = 0.64239659
Iteration 55, loss = 0.64181002
Iteration 56, loss = 0.64131667
Iteration 57, loss = 0.64076423
Iteration 58, loss = 0.64029287
Iteratio

/usr/local/lib/python3.10/dist-packages/sklearn/neural_network/_multilayer_perceptron.py:686: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Iteration 30, loss = 0.68410108
Iteration 31, loss = 0.68280371
Iteration 32, loss = 0.68156824
Iteration 33, loss = 0.68025509
Iteration 34, loss = 0.67894494
Iteration 35, loss = 0.67766163
Iteration 36, loss = 0.67641613
Training loss did not improve more than tol=0.000100 for 10 consecutive epochs. Stopping.
Iteration 1, loss = 11.17848883
Iteration 2, loss = 0.72929249
Iteration 3, loss = 0.72582498
Iteration 4, loss = 0.72441567
Iteration 5, loss = 0.72283428
Iteration 6, loss = 0.72104165
Iteration 7, loss = 0.71913908
Iteration 8, loss = 0.71719741
Iteration 9, loss = 0.71527604
Iteration 10, loss = 0.71335357
Iteration 11, loss = 0.71118336
Iteration 12, loss = 0.70905210
Iteration 13, loss = 0.70682600
Iteration 14, loss = 0.70475904
Iteration 15, loss = 0.70265540
Iteration 16, loss = 0.70028557
Iteration 17, loss = 0.69812676
Iteration 18, loss = 0.69614440
Iteration 19, loss = 0.69423513
Iteration 20, loss = 0.69266262
Iteration 21, loss = 0.69117350
Iteration 22, loss = 0

...

Iteration 18, loss = 0.72677953
Iteration 19, loss = 0.72513847
Iteration 20, loss = 0.72325741
Iteration 21, loss = 0.72174151
Iteration 22, loss = 0.72158979
Iteration 23, loss = 0.72207366
Iteration 24, loss = 0.72154036
Iteration 25, loss = 0.72122763
Iteration 26, loss = 0.72246172
Iteration 27, loss = 0.72074979
Iteration 28, loss = 0.72003844
Iteration 29, loss = 0.72008718
Iteration 30, loss = 0.71992762
Iteration 31, loss = 0.72035164
Iteration 32, loss = 0.71946834
Iteration 33, loss = 0.71861745
Iteration 34, loss = 0.71880091
Iteration 35, loss = 0.72050861
Iteration 36, loss = 0.71976702
Iteration 37, loss = 0.71890439
Iteration 38, loss = 0.71744220
Iteration 39, loss = 0.71789834
Iteration 40, loss = 0.71758117
Iteration 41, loss = 0.71831086
Iteration 42, loss = 0.71963319
Iteration 43, loss = 0.71771348
Iteration 44, loss = 0.71631283
Iteration 45, loss = 0.71668107
Iteration 46, loss = 0.71598588
Iteration 47, loss = 0.71557338
Iteration 48, loss = 0.71618491
Iteratio

/usr/local/lib/python3.10/dist-packages/sklearn/neural_network/_multilayer_perceptron.py:686: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (450) reached and the optimization hasn't converged yet.
  warnings.warn(


Iteration 3, loss = 7.26163879
Iteration 4, loss = 0.82935075
Iteration 5, loss = 0.78433385
Iteration 6, loss = 0.78479465
Iteration 7, loss = 0.75920315
Iteration 8, loss = 0.75193119
Iteration 9, loss = 0.74658945
Iteration 10, loss = 0.74349311
Iteration 11, loss = 0.73845586
Iteration 12, loss = 0.73664965
Iteration 13, loss = 0.74943266
Iteration 14, loss = 0.74116410
Iteration 15, loss = 0.73031754
Iteration 16, loss = 0.72752236
Iteration 17, loss = 0.72806330
Iteration 18, loss = 0.72742962
Iteration 19, loss = 0.72634346
Iteration 20, loss = 0.72459774
Iteration 21, loss = 0.72400887
Iteration 22, loss = 0.72505442
Iteration 23, loss = 0.72261553
Iteration 24, loss = 0.72320879
Iteration 25, loss = 0.72262219
Iteration 26, loss = 0.72113107
Iteration 27, loss = 0.71914054
Iteration 28, loss = 0.71740812
Iteration 29, loss = 0.71686932
Iteration 30, loss = 0.71643127
Iteration 31, loss = 0.71690199
Iteration 32, loss = 0.71599670
Iteration 33, loss = 0.71587311
Iteration 34, l

/usr/local/lib/python3.10/dist-packages/sklearn/neural_network/_multilayer_perceptron.py:686: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (450) reached and the optimization hasn't converged yet.
  warnings.warn(


Görüntülenen çıkış son 5000 satıra kısaltıldı.
Iteration 58, loss = 0.69683247
Iteration 59, loss = 0.69544410
Iteration 60, loss = 0.69388425
Iteration 61, loss = 0.69593000
Iteration 62, loss = 0.69187121
Iteration 63, loss = 0.69092420
Iteration 64, loss = 0.69289453
Iteration 65, loss = 0.69054765
Iteration 66, loss = 0.68896008
Iteration 67, loss = 0.68885343
Iteration 68, loss = 0.68859799
Iteration 69, loss = 0.68808543
Iteration 70, loss = 0.68840825
Iteration 71, loss = 0.68796967
Iteration 72, loss = 0.68998494
Iteration 73, loss = 0.68905485
Iteration 74, loss = 0.68752789
Iteration 75, loss = 0.68861230
Iteration 76, loss = 0.69023407
Iteration 77, loss = 0.68840915
Iteration 78, loss = 0.68731305
Iteration 79, loss = 0.68726626
Iteration 80, loss = 0.68808144
Iteration 81, loss = 0.69201130
Iteration 82, loss = 0.68921550
Iteration 83, loss = 0.68726811
Iteration 84, loss = 0.68677245
Iteration 85, loss = 0.68593380
Iteration 86, loss = 0.68653307
Iteration 87, loss = 0.68